# Wildfires: SEVIRI

## Context
### Purpose
Explore [SEVIRI](https://www.eumetsat.int/seviri) satellite imagery and wildfire data that is open and free for scientific use.

### Sensor description
The [SEVIRI Level 1.5 Image Data](https://data.eumetsat.int/data/map/EO:EUM:DAT:MSG:HRSEVIRI) product contains provides 12 spectral channels. Level 1.5 image data corresponds to the geolocated and radiometrically pre-processed image data, ready for further processing, e.g. the extraction of meteorological products

### Highlights
* Use `satpy` to load, visualise, and regrid SEVIRI level 1.5 data.
* Fetch a fire database containing some 8080 fires from September 1st, 2020.
* Visualisation of fire pixels from the database.
* Visualisation of the fire pixels alongside bands from the SEVIRI satellite data.

### Authors
Samuel Jackson, Science & Technology Facilities Council, [@samueljackson92](https://github.com/samueljackson92)

### Reviewers
Alejandro Coca-Castro, The Alan Turing Institute, [@acocac](https://github.com/acocac), 06/09/21 (latest revision)

:::{note}
The author acknowledges [EUMETSAT]().
:::

## Install and load libraries

In [1]:
! pip -q install pyspectral
! pip -q install 'satpy==0.26.0'
! pip -q install gdown

In [2]:
import pandas as pd
import numpy as np
import geopandas
import intake
import fsspec, aiohttp
import hvplot.xarray
import hvplot.pandas
import holoviews as hv
import panel as pn
import satpy
import xarray as xr
import tempfile
from pathlib import Path
from scipy.spatial import cKDTree
from satpy.writers import get_enhanced_image
from getpass import getpass
from pathlib import Path
from pyresample import geometry
from pyresample import create_area_def
import datetime
import urllib.request
import os.path
import requests

## Fetch Data


:::{note}
To download data from the [EUMETSAT's Data site](https://data.eumetsat.int/data/map/EO:EUM:DAT:MSG:HRSEVIRI) you must have a valid account. Please register with EUMETSAT's data sevices if you do not already have an account. Then provide your consumer key and consumer secret when prompted in the cell below. Your consumer key and consumer secret can be found at the following url: https://api.eumetsat.int/api-key/
 
Now you should successfully be able to download SEVIRI data.
:::

In [3]:
consumer_key = getpass('Consumer Key: ')
consumer_secret = getpass('Consumer Secret: ')


token_url = 'https://api.eumetsat.int/token'
response = requests.post(
        token_url,
        auth=requests.auth.HTTPBasicAuth(consumer_key, consumer_secret),
        data = {'grant_type': 'client_credentials'},
        headers = {"Content-Type" : "application/x-www-form-urlencoded"}
    )

access_token = response.json()['access_token']

filename = 'MSG4-SEVI-MSG15-0100-NA-20200901104243.230000000Z-NA.nat'

product_url = 'https://api.eumetsat.int/data/download/collections/EO%3AEUM%3ADAT%3AMSG%3AHRSEVIRI/products/MSG4-SEVI-MSG15-0100-NA-20200901104243.230000000Z-NA/entry'
product_url += f'?name={filename}'
product_url += f'&access_token={access_token}'

urllib.request.urlretrieve(product_url, '../sensors/' + filename)

Consumer Key:  ····························
Consumer Secret:  ····························


('../sensors/MSG4-SEVI-MSG15-0100-NA-20200901104243.230000000Z-NA.nat',
 <http.client.HTTPMessage at 0x7f16551d31c0>)

Download the fire pixel data for this day from Google Drive. This data is not directly downloadable from the internet, so we share a subset of fires for this imagey here.

In [4]:
!gdown --id 1A5CMPaWDsJUa32j3N7qB7iLLUh4qwymD

Downloading...
From: https://drive.google.com/uc?id=1A5CMPaWDsJUa32j3N7qB7iLLUh4qwymD
To: /home/lhs18285/git/environmental-ai-book/book/wildfires/sensors/HDF5_LSASAF_MSG_FRP-PIXEL-ListProduct_MSG-Disk_202009011045
100%|████████████████████████████████████████| 130k/130k [00:00<00:00, 20.7MB/s]


Load an intake catalog for the downloaded data

In [5]:
path = Path(tempfile.mkdtemp())
catalog_file = path / 'catalog.yaml'

with catalog_file.open('w') as f:
    f.write('''
sources:
    seviri_l1b:
      args:
        urlpath: 'MSG4-SEVI-MSG15-0100-NA-20200901104243.230000000Z-NA.nat'
        reader: 'seviri_l1b_native'
      description: "SEVIRI Level 1.5 Products"
      driver: SatpySource
      metadata: {}
    seviri_fires:
      args:
        urlpath: 'HDF5_LSASAF_MSG_FRP-PIXEL-ListProduct_MSG-Disk_202009011045'
      description: "SEVIRI Level 2 Fires"
      driver: netcdf
      metadata: {}
''')

In [6]:
from intake.source.base import PatternMixin
from intake.source.base import DataSource, Schema

import glob

class SatpySource(DataSource, PatternMixin):
    """Intake driver for data supported by satpy.Scene"""
    
    container = 'python'
    name = 'satpy'
    version = '0.0.1'
    partition_access = False

    def __init__(self, urlpath, reader=None, metadata=None, path_as_pattern=True):
        """
        Parameters
        ----------
        path: str, location of model pkl file
        Either the absolute or relative path to the file
        opened. Some examples:
          - ``{{ CATALOG_DIR }}/file.nat``
          - ``{{ CATALOG_DIR }}/*.nc``
        reader: str, optional
        Name of the satpy reader to use when loading data (ie. ``modis_l1b``)
        metadata: dict, optional
        Additional metadata to pass to the intake catalog
        path_as_pattern: bool or str, optional
        Whether to treat the path as a pattern (ie. ``data_{field}.nc``)
        and create new coodinates in the output corresponding to pattern
        fields. If str, is treated as pattern to match on. Default is True.
        """

        self.path_as_pattern = path_as_pattern
        self.urlpath = urlpath
        self._reader = reader
        super(SatpySource, self).__init__(metadata=metadata)

    def _load(self):
        files = self.urlpath
        files = list(glob.glob(files))
        return satpy.Scene(files, reader=self._reader)
    
    def _get_schema(self):
        self._schema = Schema(
            npartitions=1,
            extra_metadata={}
        )
        return self._schema

    def read(self):
        self._load_metadata()
        return self._load()

intake.register_driver('SatpySource', SatpySource, overwrite=True)
cat = intake.open_catalog(catalog_file)

## Load SEVIRI Satellite Data

Here we use `satpy` to load the SEVIRI level 1b data into memory. As well as loading the image data, `satpy` provides a easy way to regrid the data to different coordinate systems.

In [7]:
scn = cat['seviri_l1b'].read()
scn

In [ ]:
scn.load(['natural_color', 'IR_039', 'IR_108'])
scn.show('natural_color')

### Resample to a different projection

In the plot above you can see that the raw SEVIRI data has distortion towards edge of the image. By regridding the data we can avoid some of this distortion.

In [9]:
area_id = "Southern Africa"
description = "Southern Africa in Mercator-Projection"
proj_id = "Southern Africa"
proj_dict = {"proj": "eqc"}

width = 1000    # width of the result domain in pixels
height = 1000   # height of the result domain in pixels

llx =  0    # projection x coordinate of lower left corner of lower left pixel
lly =  -30e5  # projection y coordinate of lower left corner of lower left pixel
urx =  55e5   # projection x coordinate of upper right corner of upper right pixel
ury =  10e5   # projection y coordinate of upper right corner of upper right pixel

area_extent = (llx,lly,urx,ury)

resolution=3000
center =(0,0)
area_def = create_area_def(area_id, proj_dict, resolution=resolution, area_extent=area_extent)

seviri_scn = scn.resample(area_def, radius_of_influence=10000)

Rounding shape to (1334, 1834) and resolution from (3000.0, 3000.0) meters to (2998.909487459106, 2998.5007496251874) meters
/home/lhs18285/miniconda3/envs/pangeo/lib/python3.9/site-packages/pyproj/crs/crs.py:1216: UserWarning: You will likely lose important projection information when converting to a PROJ string from another format. See: https://proj.org/faq.html#what-is-the-best-format-for-describing-coordinate-reference-systems
  return self._crs.to_proj4(version=version)
/home/lhs18285/miniconda3/envs/pangeo/lib/python3.9/site-packages/pyproj/crs/crs.py:1216: UserWarning: You will likely lose important projection information when converting to a PROJ string from another format. See: https://proj.org/faq.html#what-is-the-best-format-for-describing-coordinate-reference-systems
  return self._crs.to_proj4(version=version)


In [ ]:
seviri_scn.show('natural_color')

## Load SEVIRI Fire Database

Now we're going to load the SEVIRI fire database from HDF file. This contains the longitude, latitude, and time of where fires have been detected to occur. It also includes an estimate of the Fire Radiative Power (FRP), a measure of the intensity of the fire, for each fire detected.

In [11]:
# Scale factors for the SEVIRI fire product from:
# https://nextcloud.lsasvcs.ipma.pt/s/CZa8RwDxjGqYezS?dir=undefined&openfile=105793

SCALE_FACTORS = dict(
    FRP=10,
    FRP_UNCERTAINTY=100,
    ERR_FRP_COEFF=10000,
    ERR_BACKGROUND=10000,
    ERR_ATM_TRANS=10000,
    ERR_VERT_COMP=10000,
    ERR_RADIOMETRIC=10000,
    LATITUDE=100,
    LONGITUDE=100,
    FIRE_CONFIDENCE=100,
    BT_MIR=10,
    BT_TIR=10,
    BW_BT_MIR=10,
    BW_BTD=10,
    PIXEL_SIZE=100,
    PIXEL_VZA=100,
    PIXEL_ATM_TRANS=10000,
    RAD_PIX=10000,
    STD_BCK=10000
)

def process_fire_product(fire_pixels):
    # Hack: xarray randomly loads some columns as coordinates, which don't get converted to a dataframe
    # Correct here by removing them as coords and renaming them back to their original name
    coords = list(fire_pixels.coords.keys())
    fire_pixels = fire_pixels.reset_index(coords).reset_coords()
    fire_pixels = fire_pixels.swap_dims({key: f'phony_dim_0' for key in list(fire_pixels.dims.keys())})
    fire_pixels = fire_pixels.rename({f"{name}_": name for name in coords})
    fire_pixels = fire_pixels.to_dataframe()

    for c in fire_pixels.columns:
        if c in SCALE_FACTORS:
            fire_pixels[c] = fire_pixels[c] / SCALE_FACTORS[c]
        
    fire_pixels['ABS_LINE_1KM'] = fire_pixels.ABS_LINE // 2
    fire_pixels['ABS_PIXEL_1KM'] = fire_pixels.ABS_PIXEL // 2
    fire_pixels.index.name = 'index'
    return fire_pixels

def parse_l2_timestamp(product_name):
    """Parse the timestamp from the SEVIRI L2 product name"""
    timestamp = product_name.split('_')[-1]
    timestamp = pd.to_datetime(timestamp, format='%Y%m%d%H%M')
    return timestamp

# Read in fires, scale and rename dimensions
fires = cat['seviri_fires'].read()
fires = process_fire_product(fires)
fires = fires.rename({'LONGITUDE': 'longitude', 'LATITUDE': 'latitude', 'FRP': 'frp'}, axis=1)

# Grab the timestamp of the product
urlpath = cat['seviri_fires'].describe()['args']['urlpath']
fires['timestamp'] = parse_l2_timestamp(urlpath)

# Convert to geopandas
fires = geopandas.GeoDataFrame(
    fires, geometry=geopandas.points_from_xy(fires.longitude, fires.latitude))

# We're only interested in data from Southern Africa for now
llx =  0    # projection x coordinate of lower left corner of lower left pixel
lly =  -30  # projection y coordinate of lower left corner of lower left pixel
urx =  55   # projection x coordinate of upper right corner of upper right pixel
ury =  10   # projection y coordinate of upper right corner of upper right pixel

fires = fires.cx[llx:urx, lly:ury]
fires = fires.sort_index()
fires

ABS_LINE  ABS_PIXEL  ACQTIME  BT_MIR  BW_BTD  BW_BT_MIR  BW_NUMPIX  \
index                                                                       
6          1942       3065     1051   321.7    48.9      313.4         10   
7          1953       3110     1051   316.8    39.9      309.0         10   
8          1955       3110     1051   321.8    46.6      312.6         13   
9          1955       3111     1051   323.5    38.4      311.9         14   
10         2009       3069     1051   316.0    19.2      311.8         16   
...         ...        ...      ...     ...     ...        ...        ...   
904        2566       3166     1049   318.7    12.4      313.6         16   
905        2597       2398     1049   315.7    21.6      312.2         16   
906        2597       2399     1049   319.1    16.4      311.9         16   
907        2598       2398     1049   320.8    18.2      311.6         16   
908        2598       2399     1049   325.8    12.6      311.4         16   

       BW_SIZE  ERR_ATM_TRANS  ERR_BACKGROUND  ...  RAD_PIX  STD_BCK  BT_TIR  \
index                                          ...                             
6            5         0.1098          0.2410  ...    0.219   0.1575   313.8   
7            5         0.1071          0.2542  ...    0.184   0.1477   306.2   
8            5         0.1078          0.2245  ...    0.219   0.2502   311.5   
9            5         0.1083          0.1683  ...    0.233   0.2599   305.7   
10           5         0.1020          0.4874  ...    0.179   0.0447   311.5   
...        ...            ...             ...  ...      ...      ...     ...   
904          5         0.1476          0.4168  ...    0.196   0.0326   312.2   
905          5         0.0843          0.6242  ...    0.176   0.0800   310.0   
906          5         0.0844          0.2823  ...    0.199   0.0679   310.3   
907          5         0.0842          0.2157  ...    0.211   0.0534   310.4   
908          5         0.0843          0.1239  ...    0.252   0.0381   310.3   

       ERR_RADIOMETRIC    frp  latitude  ABS_LINE_1KM  ABS_PIXEL_1KM  \
index                                                                  
6               0.3250  125.9     -2.40           971           1532   
7               0.3382  104.8     -2.72           976           1555   
8               0.3085  137.0     -2.78           977           1555   
9               0.2523  178.6     -2.78           977           1555   
10              0.5714   58.0     -4.30          1004           1534   
...                ...    ...       ...           ...            ...   
904             0.5008  105.4    -20.99          1283           1583   
905             0.7082   37.2    -20.95          1298           1199   
906             0.3663   81.3    -20.95          1298           1199   
907             0.2997  105.4    -20.98          1299           1199   
908             0.2079  181.6    -20.98          1299           1199   

                timestamp                    geometry  
index                                                  
6     2020-09-01 10:45:00   POINT (36.19000 -2.40000)  
7     2020-09-01 10:45:00   POINT (37.93000 -2.72000)  
8     2020-09-01 10:45:00   POINT (37.93000 -2.78000)  
9     2020-09-01 10:45:00   POINT (37.97000 -2.78000)  
10    2020-09-01 10:45:00   POINT (36.44000 -4.30000)  
...                   ...                         ...  
904   2020-09-01 10:45:00  POINT (44.54000 -20.99000)  
905   2020-09-01 10:45:00  POINT (16.11000 -20.95000)  
906   2020-09-01 10:45:00  POINT (16.14000 -20.95000)  
907   2020-09-01 10:45:00  POINT (16.12000 -20.98000)  
908   2020-09-01 10:45:00  POINT (16.14000 -20.98000)  

[880 rows x 29 columns]

### Geographical distribution of Fires

Here we plot the geographical distribution of fires detected by SEVIRI over Southern Africa.

In [12]:
fires.hvplot.points('longitude', 'latitude', c='frp', geo=True, alpha=0.2,
                    tiles='ESRI', xlim=(llx, urx), ylim=(lly, ury), cmap='autumn', logz=True,
                    dynamic=False)

:Overlay
   .Tiles.I  :Tiles   [x,y]
   .Points.I :Points   [longitude,latitude]   (frp)

## Visualising Fire Pixels with Satellite Imagery

Visualise a color image of the SEVIRI region using `hvplot`.

In [13]:
seviri_dataset = seviri_scn.to_xarray_dataset()

img = get_enhanced_image(seviri_scn['natural_color'].squeeze())
img = img.data
img = img.clip(0, 1)
img = (img * 255).astype(np.uint8)

seviri_dataset['natural_color'] = img

grid = seviri_scn.min_area().get_lonlats()
lons, lats = grid[0][0], grid[1][:, 0]
seviri_dataset = seviri_dataset.assign_coords(dict(x=lons, y=lats))
seviri_dataset = seviri_dataset.rename(dict(x='longitude', y='latitude'))

rgb = seviri_dataset['natural_color'].hvplot.rgb(x='longitude', y='latitude', bands='bands', rasterize=True, data_aspect=1)
rgb

/home/lhs18285/miniconda3/envs/pangeo/lib/python3.9/site-packages/pyproj/crs/crs.py:1216: UserWarning: You will likely lose important projection information when converting to a PROJ string from another format. See: https://proj.org/faq.html#what-is-the-best-format-for-describing-coordinate-reference-systems
  return self._crs.to_proj4(version=version)
/home/lhs18285/miniconda3/envs/pangeo/lib/python3.9/site-packages/dask/core.py:121: RuntimeWarning: invalid value encountered in cos
  return func(*(_execute_task(a, cache) for a in args))
/home/lhs18285/miniconda3/envs/pangeo/lib/python3.9/site-packages/dask/core.py:121: RuntimeWarning: invalid value encountered in sin
  return func(*(_execute_task(a, cache) for a in args))
/home/lhs18285/miniconda3/envs/pangeo/lib/python3.9/site-packages/dask/core.py:121: RuntimeWarning: invalid value encountered in log
  return func(*(_execute_task(a, cache) for a in args))
/home/lhs18285/miniconda3/envs/pangeo/lib/python3.9/site-packages/dask/core.py

:DynamicMap   []
   :RGB   [longitude,latitude]   (R,G,B)

Now overlay the fire pixels ontop of the SEVIRI image, along with the FRP for each fire pixel. Try zooming in with `rasterize=False`, you should be able to see clear smoke trails at the locations of some of the fires!

In [14]:
rgb = seviri_dataset['natural_color'].hvplot.rgb(x='longitude', y='latitude', bands='bands', data_aspect=1, hover=False, title='True Colour', rasterize=True)
points = fires.hvplot.points('longitude', 'latitude', c='frp', cmap='autumn', logz=True, alpha=0.4)
rgb*points

/home/lhs18285/miniconda3/envs/pangeo/lib/python3.9/site-packages/dask/core.py:121: RuntimeWarning: invalid value encountered in cos
  return func(*(_execute_task(a, cache) for a in args))
/home/lhs18285/miniconda3/envs/pangeo/lib/python3.9/site-packages/dask/core.py:121: RuntimeWarning: invalid value encountered in sin
  return func(*(_execute_task(a, cache) for a in args))
/home/lhs18285/miniconda3/envs/pangeo/lib/python3.9/site-packages/dask/core.py:121: RuntimeWarning: invalid value encountered in log
  return func(*(_execute_task(a, cache) for a in args))
/home/lhs18285/miniconda3/envs/pangeo/lib/python3.9/site-packages/dask/core.py:121: RuntimeWarning: invalid value encountered in cos
  return func(*(_execute_task(a, cache) for a in args))
/home/lhs18285/miniconda3/envs/pangeo/lib/python3.9/site-packages/dask/core.py:121: RuntimeWarning: invalid value encountered in sin
  return func(*(_execute_task(a, cache) for a in args))
/home/lhs18285/miniconda3/envs/pangeo/lib/python3.9/sit

:DynamicMap   []
   :Overlay
      .RGB.I    :RGB   [longitude,latitude]   (R,G,B)
      .Points.I :Points   [longitude,latitude]   (frp)

We can also overlay the fire pixels ontop of the band difference between SEVIRI 3.9 and 10.8 micron wavelength bands. The 3.9 and 10.8 bands are thermal bands. Fires will appear as very bright pixels in the difference between these two bands. Try zooming in with `rasterize=False`, you should be able to clearly see bright spots at the location of each fire pixel.

In [15]:
band_difference = seviri_dataset['IR_039'] - seviri_dataset['IR_108']
rgb = band_difference.hvplot.image(x='longitude', y='latitude', cmap='viridis', data_aspect=1, hover=False, title='Band 20: 3.7 micron', rasterize=True)
points = fires.hvplot.points('longitude', 'latitude', c='frp', cmap='autumn', logz=True, alpha=0.4)
rgb*points

:DynamicMap   []
   :Overlay
      .Image.I  :Image   [longitude,latitude]   (value)
      .Points.I :Points   [longitude,latitude]   (frp)

## Summary

This notebook has demonstrated the use of:
 - The `satpy` package to easily load, plot and regrid satellite data from the SEVIRI sensor.
 - `hvplot` to interatively visualise wildfire pixels detected from the SEVIRI sensor.
 - `geopandas` to load, filter, and manipulate historical wildfire pixel data.